---
# Create ESMF mesh file for running WW3 for CESM3 LGM
- Author: Jiang Zhu (jiangzhu@ucar.edu)
- Tools used
  - [pop_tools](https://pop-tools.readthedocs.io/en/latest/) to get gx3v7 grid
  - xesmf to regrid MOM6 LGM topo into gx3v7
  - This step depends on the LGM Topo file from create_mom6_bathy.ipynb
  - UXarray for visualization of the mesh file
---

In [1]:
import datetime
import os

import numpy as np
import xarray as xr
import uxarray as ux
import xesmf

import pop_tools

import warnings
warnings.filterwarnings('ignore')

/glade/u/apps/opt/conda/envs/npl-2025b/lib/python3.12/site-packages/pop_tools/__init__.py:4: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  from pkg_resources import DistributionNotFound, get_distribution


---
## Input files
- WW3 mesh file for preindustrial, elementMask of which will be updated
- LGM topography file for MOM6 to get an LGM land-sea mask
- Standard gx3v7 grid for regridding

In [2]:
ww3_mesh_pre = '/glade/campaign/cesm/cesmdata/inputdata/share/meshes/wgx3v7_240327_ESMFmesh.nc'
ds_mesh_pre = xr.open_dataset(ww3_mesh_pre)
ds_mesh_pre

<xarray.Dataset> Size: 895kB
Dimensions:         (nodeCount: 11700, coordDim: 2, elementCount: 11600,
                     maxNodePElement: 4)
Dimensions without coordinates: nodeCount, coordDim, elementCount,
                                maxNodePElement
Data variables:
    nodeCoords      (nodeCount, coordDim) float64 187kB ...
    elementConn     (elementCount, maxNodePElement) float64 371kB ...
    numElementConn  (elementCount) int8 12kB ...
    centerCoords    (elementCount, coordDim) float64 186kB ...
    elementArea     (elementCount) float64 93kB ...
    elementMask     (elementCount) int32 46kB ...
Attributes:
    gridType:       unstructured mesh
    version:        0.9
    inputFile:      gx3v7_120309.nc
    timeGenerated:  Mo

In [3]:
mom_topo_lgm = '/glade/work/jiangzhu/data/inputdata/mom/tx2_3v2/ocean_topo_tx2_3v2_240501_21ka_250922.nc'
ds_mom_lgm = xr.open_dataset(mom_topo_lgm).rename({'y': 'lat', 'x': 'lon'})
ds_mom_lgm

<xarray.Dataset> Size: 6MB
Dimensions:  (ny: 480, nx: 540)
Dimensions without coordinates: ny, nx
Data variables:
    lat      (ny, nx) float64 2MB ...
    lon      (ny, nx) float64 2MB ...
    mask     (ny, nx) int32 1MB ...
    depth    (ny, nx) float32 1MB ...
Attributes:
    date_created:  2025-09-22T12:22:04.264856
    title:         LGM bathymetry file for MOM6 by Jiang Zhu (jiangzhu@ucar.e...
    min_depth:     2.5
    max_depth:     8008.71923828125

In [4]:
ds_gx3 = pop_tools.get_grid('POP_gx3v7')
ds_gx3['lat'] = ds_gx3.TLAT
ds_gx3['lon'] = ds_gx3.TLONG
ds_gx3

<xarray.Dataset> Size: 1MB
Dimensions:      (nlat: 116, nlon: 100, z_t: 60, z_w: 60, z_w_bot: 60)
Coordinates:
  * z_t          (z_t) float64 480B 500.0 1.5e+03 ... 5.125e+05 5.375e+05
  * z_w          (z_w) float64 480B 0.0 1e+03 2e+03 ... 4.75e+05 5e+05 5.25e+05
  * z_w_bot      (z_w_bot) float64 480B 1e+03 2e+03 3e+03 ... 5.25e+05 5.5e+05
Dimensions without coordinates: nlat, nlon
Data variables: (12/15)
    TLAT         (nlat, nlon) float64 93kB -79.5 -79.5 -79.5 ... 68.26 68.21
    TLONG        (nlat, nlon) float64 93kB 323.3 326.9 330.5 ... 319.3 320.8
    ULAT         (nlat, nlon) float64 93kB -78.73 -78.73 -78.73 ... 68.42 68.4
    ULONG        (nlat, nlon) float64 93kB 325.1 328.7 332.3 ... 320.1 321.5
    DXT          (nlat, nlon) float64 93kB 6.842e+06 6.828e+06 ... 6.129e+06
    DYT          (nlat, nlon) float64 93kB 1.686e+07 1.686e+07 ... 4.524e+06
    ...           ...
    UAREA        (nlat, nlon) float64 93kB 1.318e+14 1.318e+14 ... 6.27e+13
    KMT          (nlat, nlon) int32 46kB 0 0 0 0 0 0 0 0 0 ... 0 0 0 0 0 0 0 0 0
    REGION_MASK  (nlat, nlon) int32 46kB 0 0 0 0 0 0 0 0 0 ... 0 0 0 0 0 0 0 0 0
    dz           (z_t) float64 480B 1e+03 1e+03 1e+03 ... 2.5e+04 2.5e+04
    lat          (nlat, nlon) float64 93kB -79.5 -79.5 -79.5 ... 68.26 68.21
    lon          (nlat, nlon) float64 93kB 323.3 326.9 330.5 ... 319.3 320.8
Attributes:
    lateral_dims:       [116, 100]
    vertical_dims:      60
    vert_grid_file:     gx3v7_vert_grid
    horiz_grid_fname:   inputdata/ocn/pop/gx3v7/grid/horiz_grid_20030806.ieeer8
    topography_fname:   inputdata/ocn/pop/gx3v7/grid/topography_20100105.ieeei4
    region_mask_fname:  inputdata/ocn/pop/gx3v7/grid/region_mask_20090831.ieeei4
    type:               dipole
    title:              POP_gx3v7 grid

---
## Output mesh file
- We only need to update the land-sea mask, `elementMask`

In [5]:
today = datetime.date.today().strftime("%y%m%d")
print(today)

filename = os.path.basename(ww3_mesh_pre)
new_filename = filename.replace(".nc", f"_21ka_{today}.nc")

work_dir = '/glade/work/jiangzhu/data/inputdata/mom/tx2_3v2'
ww3_mesh_lgm = f"{work_dir}/{new_filename}"
print(ww3_mesh_lgm)

250922
/glade/work/jiangzhu/data/inputdata/mom/tx2_3v2/wgx3v7_240327_ESMFmesh_21ka_250922.nc


---
## Step 1: Use LGM topo to create a land-sea mask to update that in the preindustrial mesh

### Regrid MOM6 `depth` to gx3v7

In [6]:
%%time

regridder = xesmf.Regridder(
    ds_mom_lgm,
    ds_gx3,
    method="bilinear",
    periodic=True)

depth_lgm = regridder(ds_mom_lgm.depth)
depth_lgm

CPU times: user 3.04 s, sys: 155 ms, total: 3.2 s
Wall time: 3.19 s


<xarray.DataArray (nlat: 116, nlon: 100)> Size: 46kB
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)
Dimensions without coordinates: nlat, nlon
Attributes:
    regrid_method:  bilinear

### Update `elementMask` in the preindustrial mesh file

In [7]:
mask_pre = ds_mesh_pre.elementMask
mask_lgm = np.where(depth_lgm > 0, 1, 0).flatten().astype(np.int32)

ds_mesh_lgm = ds_mesh_pre.copy(deep=True)
ds_mesh_lgm.elementMask.data = np.where(mask_lgm == 0, 0, mask_pre)

ds_mesh_lgm.attrs['Title']  = 'ESMF mesh for running WW3 in gx3v7 for CESM3 LGM'
ds_mesh_lgm.attrs['Author'] = 'Jiang Zhu (jiangzhu@ucar.edu)'
ds_mesh_lgm.attrs["Source_topo_file"] = mom_topo_lgm
ds_mesh_lgm.attrs['Script'] = 'create_wave_mesh.ipynb'
ds_mesh_lgm.attrs['More_info'] = 'https://github.com/NCAR/paleowg-recipes/cesm3_lgm'
ds_mesh_lgm.attrs["Date_created"] = datetime.datetime.now().isoformat()

ds_mesh_lgm.to_netcdf(ww3_mesh_lgm, format="NETCDF3_64BIT")

---
## Step 2: Use UXarray to make plot to check results

In [8]:
ds_mesh_pre = ux.open_dataset(ww3_mesh_pre, ww3_mesh_pre)
ds_mesh_lgm = ux.open_dataset(ww3_mesh_lgm, ww3_mesh_lgm)

p1 = ds_mesh_pre.elementMask.plot().opts(
    height=400, width=600, title='mask in PI mesh')

p2 = ds_mesh_lgm.elementMask.plot().opts(
    height=400, width=600, title='mask in LGM mesh')

p3 = (ds_mesh_lgm.elementMask - ds_mesh_pre.elementMask).plot(
    cmap='BuRd_r').opts(height=400, width=600, title='diff')

p = p1 + p2 + p3
p

:Layout
   .Image.I   :Image   [x,y]   (x_y elementMask)
   .Image.II  :Image   [x,y]   (x_y elementMask)
   .Image.III :Image   [x,y]   (x_y elementMask)